In [47]:
import numpy as np
import pandas as pd
import csv
from faker import Faker
import random
import time

In [48]:
#ALL_DEFINED_FUNCTIONS_GOES_HERE
def dist(pos):
    [src_lat,src_lon,src_alt,dest_lat,dest_lon,dest_alt] = pos
    return np.sqrt(np.square(src_lat-dest_lat) + np.square(src_lon-dest_lon) + np.square(src_alt-dest_alt))
def calc_time(pos,speed):
    return int(dist(pos)/speed)

def intrapol(pos,vel,acc,speed,maneuver_prob,maneuver_fact,noise_fact):
    global timestep, man_steps
    [src_lat,src_lon,src_alt,dest_lat,dest_lon,dest_alt] = pos
    [x_vel,y_vel,z_vel] = vel
#     print(vel)
    [x_acc,y_acc,z_acc] = acc
    lats , lons , alts = [src_lat] , [src_lon] , [src_alt]
    man = False
    tot_time = calc_time([src_lat,src_lon,0,dest_lat,dest_lon,0],speed)
#     print(pos,vel,man_steps)
#     lat_vel = (dest_lat-src_lat)/tot_time
#     lon_vel = (dest_lon-src_lon)/tot_time
#     alt_vel = (dest_alt-src_alt)/tot_time
#     x_vel,y_vel,z_vel = lat_vel/100000, lon_vel/10000, alt_vel/100000
    i = 1
    while(i<int(tot_time/timestep)):
#         print(pos)
#         print(man ,y_vel , (dest_lon-lons[-1])/(tot_time - i*timestep),(dest_lon-lons[-1],dest_lon,lons[-1]),(tot_time - i*timestep))
        print(lats[-1],lons[-1],alts[-1])
        if(man == True):
#             print(lats[-1],lons[-1],alts[-1])
            if(int(tot_time - i*timestep) > man_steps):
                x_vel = x_vel + (random.random() - 0.5)*2*maneuver_fact
                y_vel = y_vel + (random.random() - 0.5)*2*maneuver_fact
                z_vel = z_vel + (random.random() - 0.5)*2*maneuver_fact
                for k in range(man_steps):            
                    lats.append(lats[-1] + x_vel*timestep)
                    lons.append(lons[-1] + y_vel*timestep)
                    alts.append(alts[-1] + z_vel*timestep)
                man = False
                i = i + man_steps
        else:
#             print(lats[-1],lons[-1],alts[-1])
            lats.append(lats[-1] + x_vel*timestep)
            lons.append(lons[-1] + y_vel*timestep)
            alts.append(alts[-1] + z_vel*timestep)
#             x_velp = x_vel
#             print(x_velp ,x_vel)
            x_vel = x_vel + (lats[-1]-dest_lat)/(tot_time - i*timestep)/100000 + (random.random()-0.5)* 2 * noise_fact/100000
            y_vel = y_vel + (lons[-1]-dest_lon)/(tot_time - i*timestep)/100000 + (random.random()-0.5)* 2 * noise_fact/100000
            z_vel = z_vel + (alts[-1]-dest_alt)/(tot_time - i*timestep)/100000 + (random.random()-0.5)* 2 * noise_fact/100000
            man = (random.random() <= maneuver_prob)
            i = i + 1
    lats.append(dest_lat)
    lons.append(dest_lon)
    alts.append(dest_alt)
    return {"pos":[lats,lons,alts],"vel":[x_vel,y_vel,z_vel]}

In [49]:
#all instantiation of classes goes here
fake = Faker()

In [50]:
#the rand factor is used for deviation in the path of the flight
rand_factor = 1/100       # 1/100 will include a maximum noice of 1000 Mts (basically rand_factor*1L)
print(random.random()*rand_factor)

0.007068236582394718


In [51]:
print("Give the corresponding values")
print("<lat,lon,alt pairs> <totaltime in s> <total datapoints>")
# ipt = input()
# [m,t,n] = ipt.split(" ")
# m = int(m)
# t = int(t)
# n = int(n)
timestep = 1
man_steps = 5
m = 20
t = 3600
# n = 3600
speed = 30 / 100000
avg_alt = 5000 / 100000
alt_var = 250 / 100000
take_off = False
maneuver = 0 #To be given a value between 0 and 1 like a boolean and intermediate values will define that much degree of maneuver
fighter = True
maneuver_fact = maneuver * 2 / 1000
maneuver_prob = 0 #set this to be the number of times your plane has to maneuver per 1 move setting this to zero will make no maneuver and 1 will make random motion towards the target dest
regular_time = True

Give the corresponding values
<lat,lon,alt pairs> <totaltime in s> <total datapoints>


In [57]:
#defining the source and destination in a random manner for now
#can be changed to some other method to make it some other small distance flyable objects
src_lat, src_lon , d_lat , d_lon = float(fake.latitude()), float(fake.longitude()), float(fake.latitude()), float(fake.longitude())

In [58]:
#defining the path of latitude

print(np.linspace(float(src_lat),float(d_lat),20))
pts_lat=[src_lat]
for i in range(m):
    new_src_lat = src_lat+(d_lat-src_lat+random.random()*rand_factor)/(m-i+1)
    pts_lat.append(new_src_lat)
    src_lat = new_src_lat
pts_lat.append(d_lat)
print(pts_lat)


#Defining the path of longitude

print(np.linspace(float(src_lon),float(d_lon),20))
pts_lon=[src_lon]
for i in range(m):
    new_src_lon = src_lon+(d_lon-src_lon+random.random()*rand_factor)/(m-i+1)
    pts_lon.append(new_src_lon)
    src_lon = new_src_lon
pts_lon.append(d_lon)
print(pts_lon)

[ 38.913985    35.21275566  31.51152632  27.81029697  24.10906763
  20.40783829  16.70660895  13.00537961   9.30415026   5.60292092
   1.90169158  -1.79953776  -5.50076711  -9.20199645 -12.90322579
 -16.60445513 -20.30568447 -24.00691382 -27.70814316 -31.4093725 ]
[38.913985, 35.56569942406231, 32.21699755463328, 28.8683127854523, 25.51977946066746, 22.171367588552453, 18.822895142623263, 15.474232215692584, 12.12611439604421, 8.777577495507384, 5.42943250877752, 2.0811217192296305, -1.2675165866703848, -4.616514953967538, -7.964863965510009, -11.313234646342998, -14.661834922963113, -18.010225555570052, -21.359360126789436, -24.70648176428916, -28.057523440358295, -31.4093725]
[79.196859   77.31937305 75.44188711 73.56440116 71.68691521 69.80942926
 67.93194332 66.05445737 64.17697142 62.29948547 60.42199953 58.54451358
 56.66702763 54.78954168 52.91205574 51.03456979 49.15708384 47.27959789
 45.40211195 43.524626  ]
[79.196859, 77.49834778327273, 75.79996850538842, 74.10127558181212,

In [59]:
orig_lat = []
orig_lon = []
orig_alt = []
alt_src = avg_alt + (random.random()-0.5)*2*alt_var
if(take_off == False):
    vel = [random.random()*speed,None,0]
    vel[1] = np.sqrt(speed - np.square(vel[0]))
#     vel = [0,0,0]
#     print(vel)
    acc = [0,0,0]
    for i in range(len(pts_lat)-1):
        # print(pts_lat[i],pts_lat[i+1])
        alt_dst = avg_alt + (random.random()-0.5)*2*alt_var
        pos = [pts_lat[i],pts_lon[i],alt_src,pts_lat[i+1],pts_lon[i+1],alt_dst]
#         print(pos,vel,acc,speed,maneuver_prob,maneuver_fact)
        print("========================"+str((pts_lat[i],pts_lon[i]))+"=========================================")
        res = intrapol(pos,vel,acc,speed,maneuver_prob,maneuver_fact,0.5)
        vel = res["vel"]
        vect = res["pos"]
        orig_lat.extend(vect[0])
        orig_lon.extend(vect[1])
        orig_alt.extend(vect[2])
        
else:
    for i in range(len(pts_lat)-3):
        pass
# print(len(orig_lat))

========================(38.913985, 79.196859)=========================================
38.913985 79.196859 0.04821899041247407
38.91406929900491 79.21417930293262 0.04821899041247407
38.914150945437406 79.23149727542716 0.04822324822145879
38.91423363483755 79.24881981576081 0.04823110647529858
38.91431491247076 79.26614556810854 0.04823643267527985
38.91439758024575 79.28346976557397 0.04823869812067571
38.91448470290022 79.30079050450762 0.04824307986209825
38.91456895072493 79.31811004858415 0.04825145804613117
38.91465785863238 79.33543172201837 0.04826323897709223
38.91474620366117 79.35275553442739 0.04827499813361386
38.91483120914949 79.37008291745656 0.04828817924592803
38.914914149566776 79.38741253112526 0.04830013818076828
38.91499424882969 79.40473861546256 0.04831230427212519
38.91507386506732 79.42206169105728 0.048322867571168646
38.91514884628092 79.43938263728481 0.048328695370727065
38.91521919541159 79.45670677915065 0.0483359723912316
38.915284682920706 79.4740323

38.972070558121864 90.86932252636225 0.047550172532994484
38.97220573032411 90.88676172663402 0.047500007323908355
38.972336707902194 90.90420095371641 0.047445970509509154
38.97247258106868 90.92164321566362 0.047390777773015924
38.9726127589817 90.93908819209702 0.0473343052590816
38.97275065586481 90.95653152152758 0.047275262565226524
38.97289193949467 90.97397721508453 0.04721644003450018
38.97303097365466 90.99141993631495 0.0471624480606818
38.97316586319102 91.00885876942992 0.04711293128973085
38.97330161167914 91.02629796168762 0.0470590638557506
38.97344146723704 91.04373840404796 0.04700557716836073
38.97357991862799 91.06118267782502 0.04694939770144838
38.97372183898912 91.07862210671915 0.046895999581918445
38.973863820595895 91.09606064282883 0.04684423440084774
38.97400226231704 91.11349473850944 0.04679497536255877
38.97414421563066 91.13092636651989 0.04674337095015993
38.97428715840545 91.14835638248087 0.04669396801243534
38.974425711697386 91.16579082574883 0.0466

39.032126196724526 101.41665082179684 0.03423478339941361
39.03220815709669 101.43413243313451 0.03422137470410036
39.032293641015194 101.45161151341682 0.03421032377094191
39.032376254930156 101.46909041523925 0.03419709794729367
39.03246020839303 101.48656610117908 0.0341837087266143
39.03254368229152 101.50404269439706 0.03416714713608128
39.03262481493894 101.52151719272408 0.034154722277321616
39.03270111494779 101.53899215296119 0.0341397190007426
39.032776337762 101.55647210586744 0.03412467871233093
39.03285443315497 101.57395054633072 0.03411310208361187
39.03293065048095 101.59142870166922 0.03410561868014586
39.03300701134663 101.60890330281907 0.034094123261553234
39.0330811226253 101.62638245570383 0.03408261961741881
39.033154817689955 101.64386176506318 0.034073245766160776
39.03322633125048 101.66134259864567 0.03406162832436247
39.03329810859174 101.67882186858158 0.03405173433840285
39.03337365979004 101.69630444226432 0.03403762601191299
39.03344808151277 101.7137918

39.04730108407438 111.92121769201263 0.0002056181058317571
39.04729214904239 111.93855365042118 0.00015291655346394534
39.047283105189024 111.95589388522669 9.823475664788566e-05
39.047272100950885 111.97323579112695 4.3205652018474894e-05
39.047263658539514 111.99057360937343 -9.478211524161616e-06
39.04725705008546 112.00791540254774 -6.02116016839933e-05
39.047245454079196 112.02526069498515 -0.00010863466982502042
39.04723095887428 112.04260838674006 -0.0001558251184304926
39.04721434717159 112.05995116536148 -0.0002027332132432292
39.04719668356439 112.0772981713671 -0.0002454613191116444
39.047181943158115 112.09464047447851 -0.00028838986288338763
39.0471627423309 112.11197974852386 -0.00032636437161438927
39.0471475610184 112.12931487501436 -0.00035977725821516386
39.04712816508066 112.14665260013106 -0.00039202773245683176
39.0471106933917 112.1639869529042 -0.0004229538308397746
39.04709205727578 112.18131848690038 -0.0004528735904438224
39.0470703041657 112.19865114675395 -0

39.03399076089356 122.7586557547591 -0.043121587337929305
39.03398481700159 122.77601444049077 -0.04327409731553175
39.033977915649174 122.79337570363629 -0.04342241118076683
39.03396786128171 122.81073493830066 -0.04357021581297239
39.033960924402386 122.82809722306186 -0.04371911577903891
39.03394994552964 122.8454621790316 -0.04386839243649198
39.03394028088368 122.86282540080046 -0.04401599416560788
39.03393423065325 122.88018843607375 -0.04416665807754229
39.03392415387656 122.89755355046864 -0.04432003281726119
39.03391314047389 122.91492080438896 -0.04447752417436646
39.033898313894795 122.93228577052074 -0.04463802683171834
39.03388391692332 122.9496492617096 -0.04480042896181019
39.033869776253965 122.96700990352642 -0.044967292157262605
39.03385446517075 122.98436979111933 -0.04513042392943481
39.03383512021007 123.00172740770532 -0.0452969405321393
39.03381354259427 123.01908641602631 -0.04545977471680695
39.033790056836104 123.0364481924608 -0.045625280001055965
39.03376476

...

152.7146883313404 17716.0878565305 21.416077030221878
152.74731041142076 17720.275415450345 21.421163174408342
152.7799350181348 17724.462995723872 21.426247963228437
152.81255969839304 17728.650594401784 21.431331353561955
152.84518532406173 17732.838215347736 21.436418286900356
152.8778068618672 17737.025852731636 21.441506806884338
152.9104284929526 17741.213510437898 21.446600043663572
152.94305090509653 17745.40118799962 21.451692500103768
152.97567710135445 17749.588888887814 21.456787360760583
153.00830559813173 17753.776614387883 21.461883819893266
153.0409313659385 17757.96436493192 21.466979144944077
153.07355267391404 17762.152138843325 21.472072771992305
153.10617363122506 17766.339938839174 21.477164102768945
153.13879575478794 17770.52775725672 21.482257256257313
153.17142008076786 17774.715598613468 21.487347104398264
153.20403976618485 17778.903461354585 21.49244084590166
153.23666224184538 17783.09134387721 21.49753960146355
153.2692885251674 17787.279252488523 21.5026

173.97249800910362 20438.68358930653 24.72565682597074
174.0052988403349 20442.886807483952 24.730780286026835
174.03810140893194 20447.09004942809 24.735908396889602
174.07090386550314 20451.293322003097 24.741038216528256
174.1037022905444 20455.49661852553 24.746172874620424
174.1365056290647 20459.699937461413 24.75130666363323
174.1693127966782 20463.90328231688 24.7564356067909
174.20211849671716 20468.10665510499 24.761561843234052
174.2349236080273 20472.31005317223 24.766687584355775
174.26772517682429 20476.51347442641 24.771818010740386
174.30052387231163 20480.716919094335 24.776953110900575
174.33332087008145 20484.920388239887 24.782088187612732
174.36611384222286 20489.12388625512 24.787219976089727
174.398903110006 20493.327408077643 24.792348357313593
174.43169093938232 20497.530952372123 24.797474161700187
174.46447736579415 20501.734526612843 24.80259598671794
174.4972601672946 20505.93813132949 24.807714395626817
174.53004612860047 20510.141763294785 24.812832400090

195.66331202346527 23223.258903081012 28.160267892963272
195.69620579154892 23227.481843686735 28.165502341557957
195.7291010391685 23231.704813422934 28.170732962971766
195.76199394816516 23235.92781568969 28.17596839619531
195.7948848070025 23240.15085321157 28.18120335515011
195.8277733573991 23244.373926866312 28.186438248907393
195.86066226832529 23248.597038307456 28.191674892176593
195.89355527054013 23252.820183995034 28.19691476438666
195.9264463348377 23257.04336438423 28.202149930826
195.95933926701852 23261.266575949394 28.207386497297268
195.99223102958499 23265.489817923513 28.21262395918948
196.025121136202 23269.71309283631 28.217857278831758
196.05801538746812 23273.93639634973 28.22308690149543
196.0909094499302 23278.159735193065 28.228319513966106
196.12380157535574 23282.383110639417 28.23355470723803
196.15669801412346 23286.606521219815 28.23879016862953
196.18959848832878 23290.829967058908 28.244027486216496
196.2225027447441 23295.053443650548 28.2492657707903

214.75970555881483 25674.32423150706 31.19740732716573
214.79281018761012 25678.568514399543 31.202601604322066
214.82591047497212 25682.81284119574 31.20780038369811
214.85901417032267 25687.057210508712 31.212998745099537
214.89211884093453 25691.30161986096 31.218200635033398
214.92522472825007 25695.546065195475 31.22340258449962
214.95832919341126 25699.7905548867 31.228604300914906
214.9914379827443 25704.035085048545 31.233802922829494
215.02454816510794 25708.279659530464 31.23900167956128
215.0576587289664 25712.524269696467 31.24420226646084
215.09076815796962 25716.768916320194 31.249402457706008
215.1238806541994 25721.013603071915 31.254603107233038
215.15699315880474 25725.25832612167 31.259802081307164
215.1901033472932 25729.50309007624 31.264999980158088
215.2232118134216 25733.747898439866 31.270195429921817
215.25632344733 25737.992745188585 31.275394093138807
215.28943090103138 25742.237630586693 31.280594712735255
215.3225392996365 25746.482558629035 31.28579315889

KeyboardInterrupt: 

In [60]:
data = np.array([(np.add(range(1,len(orig_alt)+1),time.time())).tolist(),orig_lat,orig_lon,orig_alt])
data = np.transpose(data)
print(data.shape)
data = np.multiply(data,[timestep,1,1,100000])
# print (data)

(87612, 4)


In [61]:
d = pd.DataFrame(data=data,columns = ["time(in s)","lat","lon","alt"])
print (d)
d.to_csv('t11.csv', sep=",", index=False)
# with open('t10.csv', 'w', newline='') as file:
#     writer = csv.writer(file)
# #     writer.head()
#     writer.writerows(d) #, fieldnames = ["time","lat","lon","alt"]

         time(in s)         lat           lon           alt
0      1.596363e+09   38.913985     79.196859  4.821899e+03
1      1.596363e+09   38.914069     79.214179  4.821899e+03
2      1.596363e+09   38.914151     79.231497  4.822325e+03
3      1.596363e+09   38.914234     79.248820  4.823111e+03
4      1.596363e+09   38.914315     79.266146  4.823643e+03
...             ...         ...           ...           ...
87607  1.596451e+09  214.231971  25298.738305  2.961790e+06
87608  1.596451e+09  214.260628  25302.423830  2.962240e+06
87609  1.596451e+09  214.289945  25306.193471  2.962701e+06
87610  1.596451e+09  214.320251  25310.089303  2.963177e+06
87611  1.596451e+09   15.474232     67.307587  5.002920e+03

[87612 rows x 4 columns]


In [62]:
from pyproj import Proj
p = Proj(proj='utm',zone=10,ellps='WGS84', preserve_units=False)

In [63]:
x = []
y = []
for i in range(len(data)):
    res = p(data[i,1],data[i,2])
    data[i,1] = res[0]
    data[i,2] = res[1]

In [64]:
d = pd.DataFrame(data=data,columns = ["time","x","y","z"])
print (d)
d.to_csv('test_missile.csv', sep=",", index=False)

               time             x             y             z
0      1.596363e+09  8.726088e+05  1.114570e+07  4.821899e+03
1      1.596363e+09  8.720156e+05  1.114386e+07  4.821899e+03
2      1.596363e+09  8.714225e+05  1.114201e+07  4.822325e+03
3      1.596363e+09  8.708292e+05  1.114017e+07  4.823111e+03
4      1.596363e+09  8.702359e+05  1.113833e+07  4.823643e+03
...             ...           ...           ...           ...
87607  1.596451e+09           inf           inf  2.961790e+06
87608  1.596451e+09           inf           inf  2.962240e+06
87609  1.596451e+09           inf           inf  2.962701e+06
87610  1.596451e+09           inf           inf  2.963177e+06
87611  1.596451e+09  2.172398e+06  1.193774e+07  5.002920e+03

[87612 rows x 4 columns]
